In [1]:
from ase_interface import ANIENS
from ase_interface import ensemblemolecule

import hdnntools as hdt

import numpy as np
import  ase
#from ase.build import molecule
#from ase.neb import NEB
#from ase.calculators.mopac import MOPAC
from ase.md.langevin import Langevin
from ase.md.verlet import VelocityVerlet
from ase.io.trajectory import Trajectory
from ase import units

from ase.md.velocitydistribution import MaxwellBoltzmannDistribution

from ase.optimize.fire import FIRE as QuasiNewton

from ase.md.nvtberendsen import NVTBerendsen
from ase.md import MDLogger

#from ase.neb import NEBtools
from ase.io import read, write
from ase.optimize import BFGS, LBFGS

import time

van Der Waals correction will be unavailable. Please install ased3


In [2]:
dir = '/nh/nest/u/jsmith/scratch/Research/gutzwiller_research/gutz_new_data/ML-GQMD-data-NEW/case1_test/'

# Molecule file
molfile = '/nh/nest/u/jsmith/scratch/Research/gutzwiller_research/gutz_new_data/ML-GQMD-data-NEW/case1/test_files/data-U0.001/ts0/sys-000.xyz'

# Dynamics file
xyzfile = dir + 'mdcrd.xyz'

# Trajectory file
trajfile = dir + 'traj.dat'

# Optimized structure out:
optfile = dir + 'optmol.xyz'

ntdir = '/scratch/Research/gutzwiller_research/gutz_new_data/ML-GQMD-data-NEW/case1/train_models/data-U0.001/testsets/testset0'

T = 100.0 # Temperature
dt = 0.01
C = 0.1 # Optimization convergence
steps = 40000

ntdir = '/nh/nest/u/jsmith/scratch/Research/gutzwiller_research/gutz_new_data/ML-GQMD-data-NEW/case1_test/model-gutz-U0.001-x8_3/'
cns = ntdir + 'train0/rX-2.5R_32-2.0A_a8-8.params'
sae = ntdir + 'train0/sae.dat'
nnf = ntdir + 'train'
Nn = 8

#ntdir = '/nh/nest/u/jsmith/Research/gutzwiller_research/DarwinSets/GutzTrain/train_test_U2/U2_co3/'
#cns = ntdir + 'rX-6.0A_32-4.0A_a8-8.params'
#sae = ntdir + 'sae.dat'
#nnf = ntdir + 'train'
#Nn = 5

In [3]:
# Load molecule
mol = read(molfile)
L = 10.9753
mol.set_cell(([[L, 0, 0],
               [0, L, 0],
               [0, 0, L]]))

mol.set_pbc((True, True, True))

In [4]:
# Set NC
aens = ensemblemolecule(cns, sae, nnf, Nn, 0)

# Set ANI calculator
mol.set_calculator(ANIENS(aens, energy_conversion=1.0))

In [5]:
#Set pairwise
def erg_exp (Rmag):
    return 100.0*np.exp(-3.53*Rmag)

def frc_exp (Rmag,R):
    F = -3.53*erg_exp(Rmag)*(R/Rmag)                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
    return F

mol.calc.set_pairwise(erg_exp, frc_exp)

In [6]:
# Set sigma bias potential
# alpha = 0.1 # Alpha for potential

# # Energy bias function
# def bias_Efunc(sigma):
#     return np.exp(alpha * sigma)
    
# # Force bias function
# def bias_Ffunc(sigma, dsigma):
#     return -alpha * np.exp(alpha * sigma) * dsigma
    
# # Set the bias potential
# mol.calc.set_sigmabias(bias_Efunc, bias_Ffunc, epsilon=0.01)

In [7]:
# Optimize molecule
start_time = time.time()
dyn = QuasiNewton(mol)
dyn.run(fmax=C)
print('[ANI Total time:', time.time() - start_time, 'seconds]')

# Save optimized mol
spc = mol.get_chemical_symbols()
pos = mol.get_positions(wrap=False).reshape(1,len(spc),3)

hdt.writexyzfile(optfile, pos, spc)

      Step     Time          Energy         fmax
FIRE:    0 11:46:42     -338.074389       33.7911
FIRE:    1 11:46:42     -381.901054       27.3873
FIRE:    2 11:46:42     -420.641528       22.3667
FIRE:    3 11:46:42     -454.932695       18.3922
FIRE:    4 11:46:42     -485.315029       15.2178
FIRE:    5 11:46:42     -512.246405       12.6664
FIRE:    6 11:46:42     -536.124322       10.7296
FIRE:    7 11:46:42     -557.291581        9.3593
FIRE:    8 11:46:42     -576.046100        8.2351
FIRE:    9 11:46:42     -592.653025        7.4211
FIRE:   10 11:46:42     -607.347265        6.6912
FIRE:   11 11:46:43     -620.329363        6.0361
FIRE:   12 11:46:43     -631.785697        5.4475
FIRE:   13 11:46:43     -641.891049        4.9180
FIRE:   14 11:46:43     -295.289508        3.7453
FIRE:   15 11:46:43     -301.614899       18.0074
FIRE:   16 11:46:43     -311.883848       27.6001
FIRE:   17 11:46:43     -322.130248       12.0555
FIRE:   18 11:46:43     -330.927580       23.9930
F

In [8]:
MaxwellBoltzmannDistribution(mol, 100.0 * units.kB)

# We want to run MD with constant energy using the VelocityVerlet algorithm.
dyn = VelocityVerlet(mol, dt * units.fs)

In [9]:
# Open MD output
mdcrd = open(xyzfile,'w')

# Open MD output
traj = open(trajfile,'w')

# Define the printer
def storeenergy(a=mol, d=dyn, b=mdcrd, t=traj):  # store a reference to atoms in the definition.
    """Function to print the potential, kinetic and total energy."""
    epot = a.get_potential_energy() / len(a)
    ekin = a.get_kinetic_energy() / len(a)

    Estddev =  a.calc.stddev
    Fstddev =  a.calc.Fstddev

    t.write(str(d.get_number_of_steps()) + ' ' + str(ekin / (1.5 * units.kB)) + ' ' + str(epot) + ' ' + str(ekin) + ' ' + str(epot+ekin) + ' ' +  str(Estddev) + ' ' +  str(Fstddev) + '\n')
    b.write(str(len(a)) + '\n' + str(ekin / (1.5 * units.kB)) + ' Step: ' + str(d.get_number_of_steps()) + '\n')
    c = a.get_positions(wrap=True)
    for j, i in zip(a, c):
        b.write(str('C') + ' ' + str(i[0]) + ' ' + str(i[1]) + ' ' + str(i[2]) + '\n')

    print('Step: %d Energy per atom: Epot = %.3f  Ekin = %.3f (T=%.3fK)  '
          'Etot = %.6f StdDev = %.3f FStdDev = %.3f' % (d.get_number_of_steps(), epot, ekin, ekin / (1.5 * units.kB), epot + ekin, Estddev, Fstddev))
dyn.attach(storeenergy, interval=1)

In [10]:
start_time = time.time()
dyn.run(1000000)
print('[ANI Total time:', time.time() - start_time, 'seconds]')


Step: 1 Energy per atom: Epot = -2.250  Ekin = 0.013 (T=98.634K)  Etot = -2.237449 StdDev = 0.187 FStdDev = 0.078
Step: 2 Energy per atom: Epot = -2.250  Ekin = 0.013 (T=98.629K)  Etot = -2.237450 StdDev = 0.187 FStdDev = 0.078
Step: 3 Energy per atom: Epot = -2.250  Ekin = 0.013 (T=98.622K)  Etot = -2.237450 StdDev = 0.187 FStdDev = 0.078
Step: 4 Energy per atom: Epot = -2.250  Ekin = 0.013 (T=98.612K)  Etot = -2.237450 StdDev = 0.187 FStdDev = 0.078
Step: 5 Energy per atom: Epot = -2.250  Ekin = 0.013 (T=98.599K)  Etot = -2.237450 StdDev = 0.187 FStdDev = 0.078
Step: 6 Energy per atom: Epot = -2.250  Ekin = 0.013 (T=98.584K)  Etot = -2.237451 StdDev = 0.187 FStdDev = 0.078
Step: 7 Energy per atom: Epot = -2.250  Ekin = 0.013 (T=98.566K)  Etot = -2.237451 StdDev = 0.187 FStdDev = 0.078
Step: 8 Energy per atom: Epot = -2.250  Ekin = 0.013 (T=98.546K)  Etot = -2.237450 StdDev = 0.187 FStdDev = 0.079
Step: 9 Energy per atom: Epot = -2.250  Ekin = 0.013 (T=98.523K)  Etot = -2.237450 StdDe

Step: 74 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.184K)  Etot = -2.237452 StdDev = 0.186 FStdDev = 0.079
Step: 75 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.055K)  Etot = -2.237452 StdDev = 0.185 FStdDev = 0.080
Step: 76 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.925K)  Etot = -2.237451 StdDev = 0.185 FStdDev = 0.080
Step: 77 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.794K)  Etot = -2.237451 StdDev = 0.185 FStdDev = 0.081
Step: 78 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.662K)  Etot = -2.237452 StdDev = 0.185 FStdDev = 0.081
Step: 79 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.529K)  Etot = -2.237451 StdDev = 0.185 FStdDev = 0.082
Step: 80 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.395K)  Etot = -2.237453 StdDev = 0.185 FStdDev = 0.082
Step: 81 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.261K)  Etot = -2.237452 StdDev = 0.185 FStdDev = 0.082
Step: 82 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.126K)  Etot = -2.237

Step: 146 Energy per atom: Epot = -2.248  Ekin = 0.011 (T=83.215K)  Etot = -2.237452 StdDev = 0.185 FStdDev = 0.085
Step: 147 Energy per atom: Epot = -2.248  Ekin = 0.011 (T=83.087K)  Etot = -2.237453 StdDev = 0.185 FStdDev = 0.085
Step: 148 Energy per atom: Epot = -2.248  Ekin = 0.011 (T=82.960K)  Etot = -2.237454 StdDev = 0.185 FStdDev = 0.085
Step: 149 Energy per atom: Epot = -2.248  Ekin = 0.011 (T=82.834K)  Etot = -2.237453 StdDev = 0.185 FStdDev = 0.085
Step: 150 Energy per atom: Epot = -2.248  Ekin = 0.011 (T=82.708K)  Etot = -2.237453 StdDev = 0.185 FStdDev = 0.086
Step: 151 Energy per atom: Epot = -2.248  Ekin = 0.011 (T=82.583K)  Etot = -2.237453 StdDev = 0.185 FStdDev = 0.086
Step: 152 Energy per atom: Epot = -2.248  Ekin = 0.011 (T=82.459K)  Etot = -2.237454 StdDev = 0.185 FStdDev = 0.086
Step: 153 Energy per atom: Epot = -2.248  Ekin = 0.011 (T=82.335K)  Etot = -2.237453 StdDev = 0.185 FStdDev = 0.086
Step: 154 Energy per atom: Epot = -2.248  Ekin = 0.011 (T=82.213K)  Etot

Step: 220 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=76.665K)  Etot = -2.237454 StdDev = 0.185 FStdDev = 0.085
Step: 221 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=76.627K)  Etot = -2.237453 StdDev = 0.185 FStdDev = 0.085
Step: 222 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=76.591K)  Etot = -2.237454 StdDev = 0.185 FStdDev = 0.085
Step: 223 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=76.556K)  Etot = -2.237454 StdDev = 0.185 FStdDev = 0.085
Step: 224 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=76.523K)  Etot = -2.237454 StdDev = 0.185 FStdDev = 0.085
Step: 225 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=76.492K)  Etot = -2.237454 StdDev = 0.185 FStdDev = 0.085
Step: 226 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=76.461K)  Etot = -2.237454 StdDev = 0.185 FStdDev = 0.085
Step: 227 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=76.433K)  Etot = -2.237454 StdDev = 0.185 FStdDev = 0.085
Step: 228 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=76.405K)  Etot

Step: 293 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=77.179K)  Etot = -2.237453 StdDev = 0.186 FStdDev = 0.082
Step: 294 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=77.220K)  Etot = -2.237453 StdDev = 0.186 FStdDev = 0.083
Step: 295 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=77.261K)  Etot = -2.237453 StdDev = 0.186 FStdDev = 0.083
Step: 296 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=77.303K)  Etot = -2.237453 StdDev = 0.186 FStdDev = 0.082
Step: 297 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=77.344K)  Etot = -2.237454 StdDev = 0.186 FStdDev = 0.082
Step: 298 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=77.386K)  Etot = -2.237453 StdDev = 0.186 FStdDev = 0.082
Step: 299 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=77.427K)  Etot = -2.237455 StdDev = 0.186 FStdDev = 0.082
Step: 300 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=77.469K)  Etot = -2.237454 StdDev = 0.186 FStdDev = 0.082
Step: 301 Energy per atom: Epot = -2.247  Ekin = 0.010 (T=77.511K)  Etot

...

Step: 71811 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.193K)  Etot = -2.237281 StdDev = 0.186 FStdDev = 0.079
Step: 71812 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.207K)  Etot = -2.237282 StdDev = 0.186 FStdDev = 0.079
Step: 71813 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.220K)  Etot = -2.237283 StdDev = 0.186 FStdDev = 0.079
Step: 71814 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.234K)  Etot = -2.237281 StdDev = 0.186 FStdDev = 0.079
Step: 71815 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.248K)  Etot = -2.237282 StdDev = 0.186 FStdDev = 0.079
Step: 71816 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.262K)  Etot = -2.237282 StdDev = 0.186 FStdDev = 0.079
Step: 71817 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.277K)  Etot = -2.237281 StdDev = 0.186 FStdDev = 0.079
Step: 71818 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=92.291K)  Etot = -2.237281 StdDev = 0.186 FStdDev = 0.079
Step: 71819 Energy per atom: Epot = -2.249  Ekin = 0.012

Step: 71882 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.281K)  Etot = -2.237280 StdDev = 0.186 FStdDev = 0.074
Step: 71883 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.295K)  Etot = -2.237280 StdDev = 0.185 FStdDev = 0.075
Step: 71884 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.308K)  Etot = -2.237280 StdDev = 0.185 FStdDev = 0.075
Step: 71885 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.322K)  Etot = -2.237280 StdDev = 0.185 FStdDev = 0.075
Step: 71886 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.336K)  Etot = -2.237280 StdDev = 0.185 FStdDev = 0.075
Step: 71887 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.350K)  Etot = -2.237281 StdDev = 0.185 FStdDev = 0.075
Step: 71888 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.364K)  Etot = -2.237280 StdDev = 0.185 FStdDev = 0.075
Step: 71889 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.377K)  Etot = -2.237280 StdDev = 0.185 FStdDev = 0.076
Step: 71890 Energy per atom: Epot = -2.249  Ekin = 0.012

Step: 71953 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.828K)  Etot = -2.237278 StdDev = 0.185 FStdDev = 0.084
Step: 71954 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.828K)  Etot = -2.237279 StdDev = 0.185 FStdDev = 0.084
Step: 71955 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.828K)  Etot = -2.237278 StdDev = 0.185 FStdDev = 0.084
Step: 71956 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.827K)  Etot = -2.237279 StdDev = 0.185 FStdDev = 0.084
Step: 71957 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.826K)  Etot = -2.237277 StdDev = 0.185 FStdDev = 0.084
Step: 71958 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.825K)  Etot = -2.237278 StdDev = 0.185 FStdDev = 0.084
Step: 71959 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.823K)  Etot = -2.237278 StdDev = 0.185 FStdDev = 0.084
Step: 71960 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.821K)  Etot = -2.237278 StdDev = 0.185 FStdDev = 0.085
Step: 71961 Energy per atom: Epot = -2.249  Ekin = 0.012

Step: 72023 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.478K)  Etot = -2.237276 StdDev = 0.185 FStdDev = 0.078
Step: 72024 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.467K)  Etot = -2.237276 StdDev = 0.185 FStdDev = 0.078
Step: 72025 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.455K)  Etot = -2.237275 StdDev = 0.185 FStdDev = 0.078
Step: 72026 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.445K)  Etot = -2.237277 StdDev = 0.185 FStdDev = 0.078
Step: 72027 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.434K)  Etot = -2.237277 StdDev = 0.185 FStdDev = 0.078
Step: 72028 Energy per atom: Epot = -2.249  Ekin = 0.012 (T=93.423K)  Etot = -2.237276 StdDev = 0.185 FStdDev = 0.078


KeyboardInterrupt: 